In [7]:
import pandas as pd
from bokeh.io import output_file, save, show
from bokeh.plotting import figure
from bokeh.models import ColumnDataSource, Select, HoverTool
from bokeh.layouts import column
from bokeh.io import curdoc

# Load your data
df = pd.read_csv("data_for_dashboard.csv")


# Create a ColumnDataSource from the data
source = ColumnDataSource(df)

# Create a scatter plot with Bokeh
p = figure(title="t-SNE Visualization of ALL Studies", width=900, height=700)
scatter = p.circle(x='x', y='y', source=source, size=10, color='Color', line_color='DarkSlateGrey')

# Add hover tool to show additional information
hover = HoverTool(tooltips=[("NCT ID", "@nct_id"), ("Title", "@brief_title")])
p.add_tools(hover)

# Create a dropdown widget for filtering by "cluster"
cluster_options = ['Show All'] + list(df['cluster'].unique())
cluster_select = Select(title="Cluster", value="Show All", options=cluster_options)

def select_trials():
    selected_cluster = cluster_select.value
    if selected_cluster == "Show All":
        new_data = df
    else:
        new_data = df[df['cluster'] == selected_cluster]
    return new_data, selected_cluster


def update(attr, old, new):
    new_data, selected_cluster = select_trials()
    p.title.text = f"t-SNE Visualization of {selected_cluster}" if selected_cluster != 'Show All' else "t-SNE Visualization of All Clusters"
    source.data = ColumnDataSource(new_data).data  # Update the data source


# Attach the callback to the dropdown widget
cluster_select.on_change('value', update)

# Arrange the layout
layout = column(cluster_select, p)

# Save the layout as a standalone HTML file
save(layout)

# Optionally, also show the plot in the notebook environment
show(layout)

You are generating standalone HTML/JS output, but trying to use real Python
callbacks (i.e. with on_change or on_event). This combination cannot work.

Only JavaScript callbacks may be used with standalone output. For more
information on JavaScript callbacks with Bokeh, see:

    https://docs.bokeh.org/en/latest/docs/user_guide/interaction/js_callbacks.html

Alternatively, to use real Python callbacks, a Bokeh server application may
be used. For more information on building and running Bokeh applications, see:

    https://docs.bokeh.org/en/latest/docs/user_guide/server.html

You are generating standalone HTML/JS output, but trying to use real Python
callbacks (i.e. with on_change or on_event). This combination cannot work.

Only JavaScript callbacks may be used with standalone output. For more
information on JavaScript callbacks with Bokeh, see:

    https://docs.bokeh.org/en/latest/docs/user_guide/interaction/js_callbacks.html

Alternatively, to use real Python callbacks, a Bokeh ser

In [1]:
import pandas as pd
import plotly.express as px
import plotly.graph_objects as go

# Load your data
df = pd.read_csv("data_for_dashboard.csv")

# Define the options for clusters
cluster_options = ['Show All'] + list(df['cluster'].unique())

# Create traces for each cluster
fig = go.Figure()

for cluster in cluster_options:
    if cluster == 'Show All':
        filtered_df = df
    else:
        filtered_df = df[df['cluster'] == cluster]
    
    trace = go.Scatter(
        x=filtered_df['x'], 
        y=filtered_df['y'],
        mode='markers',
        marker=dict(size=10, color=filtered_df['Color']),
        name=cluster,
        hovertext=filtered_df['brief_title'],
        visible=(cluster == 'Show All')
    )
    
    fig.add_trace(trace)

# Create dropdown buttons for each cluster
dropdown_buttons = [
    dict(
        label=cluster,
        method="update",
        args=[{"visible": [cluster == opt for opt in cluster_options]}]
    ) 
    for cluster in cluster_options
]

# Update the layout with the dropdown
fig.update_layout(
    title="t-SNE Visualization of ALL Studies",
    width=900,
    height=700,
    updatemenus=[
        dict(
            active=0,
            buttons=dropdown_buttons,
            x=0.1,
            y=1.15,
            xanchor='left',
            yanchor='top'
        )
    ]
)

fig.show()